# Modeling

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from keras.models import Sequential
from keras.layers import LSTM, GRU, SimpleRNN
from keras.layers import Dense, Dropout, Normalization, BatchNormalization, LayerNormalization, Input
from tcn import TCN, tcn_full_summary
from catboost import CatBoostRegressor


from sklearn.preprocessing import MinMaxScaler

## Prepare the Data Sets
We want to create two separate datasets; one for our CatBoost model and one for our Keras models.

In [2]:
df = pd.read_parquet("../data/structured/general/combined_data.parquet")
df = df.dropna()
df

Unit_4_Power  Unit_4_Reactive Power  \
timepoints                                                 
1970-12-19 09:51:45    262.104319               3.344630   
1970-12-19 09:51:46    262.004330               3.790223   
1970-12-19 09:51:47    261.904340               4.235817   
1970-12-19 09:51:48    261.804351               4.064759   
1970-12-19 09:51:49    261.704362               3.170510   
...                           ...                    ...   
1971-01-25 11:06:44    308.716025               3.974309   
1971-01-25 11:06:45    308.746393               4.103262   
1971-01-25 11:06:46    308.776762               4.472929   
1971-01-25 11:06:47    308.807131               4.842597   
1971-01-25 11:06:48    308.837499               5.212264   

                     Turbine_Guide Vane Opening  Turbine_Pressure Drafttube  \
timepoints                                                                    
1970-12-19 09:51:45                   82.277248                  173.989815   
1970-12-19 09:51:46                   82.274520                  174.024413   
1970-12-19 09:51:47                   82.271792                  174.059012   
1970-12-19 09:51:48                   82.269064                  174.153819   
1970-12-19 09:51:49                   82.266336                  174.422046   
...                                         ...                         ...   
1971-01-25 11:06:44                   94.425666                  157.927905   
1971-01-25 11:06:45                   94.429003                  157.974925   
1971-01-25 11:06:46                   94.432340                  158.021945   
1971-01-25 11:06:47                   94.435677                  158.068966   
1971-01-25 11:06:48                   94.439014                  158.115137   

                     Turbine_Pressure Spiral Casing  Turbine_Rotational Speed  \
timepoints                                                                      
1970-12-19 09:51:45                     5311.219755                107.964273   
1970-12-19 09:51:46                     5311.640329                107.964269   
1970-12-19 09:51:47                     5312.060902                107.964264   
1970-12-19 09:51:48                     5312.405938                107.964259   
1970-12-19 09:51:49                     5312.533396                107.964254   
...                                             ...                       ...   
1971-01-25 11:06:44                     5280.929965                108.057498   
1971-01-25 11:06:45                     5280.633358                108.057492   
1971-01-25 11:06:46                     5280.336751                108.057486   
1971-01-25 11:06:47                     5280.040144                108.057479   
1971-01-25 11:06:48                     5279.835631                108.057473   

                     Bolt_1_Tensile  Bolt_2_Tensile  Bolt_3_Tensile  \
timepoints                                                            
1970-12-19 09:51:45     1598.477449     1480.989528     1684.261611   
1970-12-19 09:51:46     1598.479316     1481.003188     1684.270504   
1970-12-19 09:51:47     1598.490184     1481.028827     1684.270683   
1970-12-19 09:51:48     1598.494073     1481.059017     1684.271062   
1970-12-19 09:51:49     1598.498916     1481.075521     1684.276622   
...                             ...             ...             ...   
1971-01-25 11:06:44     1637.386115     1504.557822     1701.651420   
1971-01-25 11:06:45     1637.365865     1504.546091     1701.654301   
1971-01-25 11:06:46     1637.384133     1504.538696     1701.656143   
1971-01-25 11:06:47     1637.357141     1504.531582     1701.662201   
1971-01-25 11:06:48     1637.344985     1504.525065     1701.658131   

                     Bolt_4_Tensile  ...  Power / vane opening  \
timepoints                           ...                         
1970-12-19 09:51:45     1601.366508  ...              3.185623   
1970-12-19 09:51:46     1601.374254 

In [3]:
y_cols = [c for c in df if c.endswith("Tensile")]
adj_cols = [c for c in df if c.endswith("Tensile_adj")]

### Create CatBoost dataset

In [4]:
extra_cols = ["seconds_since_start", "month", "day_of_month", "day_of_week"]

In [16]:
X_cols = [
    "days_since_start",
    "Turbine_Pressure Drafttube",
    "seconds_since_last_start",
    "Turbine_Pressure Spiral Casing",
    "Netto Power",
    "Turbine_Rotational Speed",
    "Unit_4_Power"
]

['days_since_start',
 'Turbine_Pressure Drafttube',
 'seconds_since_last_start', 'Netto Power', 'Turbine_Rotational Speed', 'Unit_4_Power']

In [6]:
lookback = 0

cX = df[X_cols]
#X_cols = cX.drop(columns=extra_cols).columns
for i in range(1, lookback+1):
    cX.loc[:, [f"{c} (t-{i})" for c in X_cols]] = cX[X_cols].shift(i).rename(columns={c: f"{c} (t-{i})" for c in X_cols})

cy = df[y_cols]

cX

days_since_start  Turbine_Pressure Drafttube  \
timepoints                                                          
1970-12-19 09:51:45               0.0                  173.989815   
1970-12-19 09:51:46               0.0                  174.024413   
1970-12-19 09:51:47               0.0                  174.059012   
1970-12-19 09:51:48               0.0                  174.153819   
1970-12-19 09:51:49               0.0                  174.422046   
...                               ...                         ...   
1971-01-25 11:06:44               5.0                  157.927905   
1971-01-25 11:06:45               5.0                  157.974925   
1971-01-25 11:06:46               5.0                  158.021945   
1971-01-25 11:06:47               5.0                  158.068966   
1971-01-25 11:06:48               5.0                  158.115137   

                     seconds_since_last_start  Turbine_Pressure Spiral Casing  \
timepoints                                                                      
1970-12-19 09:51:45                       1.0                     5311.219755   
1970-12-19 09:51:46                       2.0                     5311.640329   
1970-12-19 09:51:47                       3.0                     5312.060902   
1970-12-19 09:51:48                       4.0                     5312.405938   
1970-12-19 09:51:49                       5.0                     5312.533396   
...                                       ...                             ...   
1971-01-25 11:06:44                   19788.0                     5280.929965   
1971-01-25 11:06:45                   19789.0                     5280.633358   
1971-01-25 11:06:46                   19790.0                     5280.336751   
1971-01-25 11:06:47                   19791.0                     5280.040144   
1971-01-25 11:06:48                   19792.0                     5279.835631   

                     Netto Power  Turbine_Rotational Speed  Unit_4_Power  
timepoints                                                                
1970-12-19 09:51:45   258.759689                107.964273    262.104319  
1970-12-19 09:51:46   258.214106                107.964269    262.004330  
1970-12-19 09:51:47   257.668524                107.964264    261.904340  
1970-12-19 09:51:48   257.739592                107.964259    261.804351  
1970-12-19 09:51:49   258.533851                107.964254    261.704362  
...                          ...                       ...           ...  
1971-01-25 11:06:44   304.741716                108.057498    308.716025  
1971-01-25 11:06:45   304.643131                108.057492    308.746393  
1971-01-25 11:06:46   304.303833                108.057486    308.776762  
1971-01-25 11:06:47   303.964534                108.057479    308.807131  
1971-01-25 11:06:48   303.625235                108.057473    308.837499  

[1749961 rows x 7 columns]

In [7]:
def train_test_split(X, y, test_percent=0.1, offset_percent=0):
    
    test_start = int(len(df) * offset_percent)
    test_end = int(len(df) * (offset_percent + test_percent))

    X_train, X_test = X.iloc[:test_start], X.iloc[test_start:test_end]
    y_train, y_test = y.iloc[:test_start], y.iloc[test_start:test_end]
    
    return X_train, X_test, y_train, y_test

cX_train, cX_test, cy_train, cy_test = train_test_split(cX, cy, test_percent=0.1, offset_percent=0.9)

### CatBoost Modeling

In [8]:
def train_catboost(X_train, y_train, eval_set=None, params={}):
    
    model = CatBoostRegressor(**params)
    model.fit(X_train, y_train, eval_set=eval_set)
    
    return model

In [9]:
def plot_error(X_test, y_test, model):

    y_test = y_tests[j].copy()

    pred = model.predict(X_test)

    plt.subplots(figsize=(15, 10))
    plt.scatter(y_test.index, y_test, label="real", s=2)
    plt.scatter(y_test.index, pred, label="pred", s=2)
    plt.legend()
    plt.show()

In [15]:
def cv_catboost(X, y, n=4, start_offset=0.5, verbose=False, params={}):

    test_percent = (1 - start_offset) / n

    all_results = []
    for i in range(n):
        X_train, X_test, y_train, y_test = train_test_split(X,
                                                            y,
                                                            test_percent = test_percent,
                                                            offset_percent = start_offset + i*test_percent)
        y_trains = [y_train[c] for c in y_train]
        y_tests = [y_test[c] for c in y_test]

        results = []
        for j in range(len(y_trains)):
            model = CatBoostRegressor(**params)
            model.fit(X_train, y_trains[j], eval_set=(X_test, y_tests[j]), verbose=verbose)

            pred = model.predict(X_test)
            mape = 100 * ((y_tests[j] - pred).abs() / y_tests[j]).mean()
            results.append(mape)
            print(f"iteration {i}, bolt {j}: MAPE={mape}")
        all_results.append(results)
    all_results = np.array(all_results)
    
    return all_results

params = {
    "loss_function": "MAPE",
    "iterations": 200,
    "depth": 5
}

#results = cv_catboost(cX, cy, params=params, verbose=True)
#print()

# Feature optimazion

In [18]:
def feature_opt(test_cols, best_result, result_cols):
    start_result = best_result
    if len(test_cols) > 1:
        for c in test_cols:
            print(f'Dropping {c} from {X_cols}')
            result = cv_catboost(cX[test_cols].drop(columns=[c]), cy, params=params, verbose=True)
            if result.mean() < best_result:
                best_result = result.mean()
                result_cols = [col for col in X_cols if col!=c]
        if best_result == start_result:
            return best_result, result_cols
        print(f'Best mean result (So far):\nfor {best_result} in with columns: {result_cols}')
        return feature_opt(result_cols, best_result, result_cols)
    else:
        return best_result, result_cols

best_result, result_cols = feature_opt(X_cols, np.inf, [])

print(f'Best mean result for {best_result}\nFor columns: result_cols')
    


Dropping days_since_start from ['days_since_start', 'Turbine_Pressure Drafttube', 'seconds_since_last_start', 'Turbine_Pressure Spiral Casing', 'Netto Power', 'Turbine_Rotational Speed', 'Unit_4_Power']


Custom logger is already specified. Specify more than one logger at same time is not thread safe.

0:	learn: 0.0013959	test: 0.0063018	best: 0.0063018 (0)	total: 95.5ms	remaining: 19s
1:	learn: 0.0013688	test: 0.0062682	best: 0.0062682 (1)	total: 156ms	remaining: 15.4s
2:	learn: 0.0013425	test: 0.0062361	best: 0.0062361 (2)	total: 218ms	remaining: 14.3s
3:	learn: 0.0013204	test: 0.0062242	best: 0.0062242 (3)	total: 279ms	remaining: 13.7s
4:	learn: 0.0012986	test: 0.0062123	best: 0.0062123 (4)	total: 344ms	remaining: 13.4s
5:	learn: 0.0012776	test: 0.0062012	best: 0.0062012 (5)	total: 405ms	remaining: 13.1s
6:	learn: 0.0012560	test: 0.0061699	best: 0.0061699 (6)	total: 465ms	remaining: 12.8s
7:	learn: 0.0012340	test: 0.0061391	best: 0.0061391 (7)	total: 526ms	remaining: 12.6s
8:	learn: 0.0012127	test: 0.0061094	best: 0.0061094 (8)	total: 591ms	remaining: 12.5s
9:	learn: 0.0011918	test: 0.0060804	best: 0.0060804 (9)	total: 653ms	remaining: 12.4s
10:	learn: 0.0011719	test: 0.0060523	best: 0.0060523 (10)	total: 713ms	remaining: 12.3s
11:	learn: 0.0011515	test: 0.0060261	best: 0.0060261 

95:	learn: 0.0004904	test: 0.0051320	best: 0.0051320 (95)	total: 6.48s	remaining: 7.02s
96:	learn: 0.0004886	test: 0.0051316	best: 0.0051316 (96)	total: 6.55s	remaining: 6.96s
97:	learn: 0.0004868	test: 0.0051311	best: 0.0051311 (97)	total: 6.62s	remaining: 6.89s
98:	learn: 0.0004848	test: 0.0051283	best: 0.0051283 (98)	total: 6.69s	remaining: 6.82s
99:	learn: 0.0004831	test: 0.0051285	best: 0.0051283 (98)	total: 6.76s	remaining: 6.76s
100:	learn: 0.0004815	test: 0.0051262	best: 0.0051262 (100)	total: 6.83s	remaining: 6.69s
101:	learn: 0.0004796	test: 0.0051234	best: 0.0051234 (101)	total: 6.9s	remaining: 6.63s
102:	learn: 0.0004782	test: 0.0051235	best: 0.0051234 (101)	total: 6.96s	remaining: 6.56s
103:	learn: 0.0004765	test: 0.0051198	best: 0.0051198 (103)	total: 7.03s	remaining: 6.49s
104:	learn: 0.0004752	test: 0.0051197	best: 0.0051197 (104)	total: 7.1s	remaining: 6.43s
105:	learn: 0.0004734	test: 0.0051172	best: 0.0051172 (105)	total: 7.17s	remaining: 6.36s
106:	learn: 0.0004721	

189:	learn: 0.0003854	test: 0.0049430	best: 0.0049430 (189)	total: 13.2s	remaining: 696ms
190:	learn: 0.0003847	test: 0.0049431	best: 0.0049430 (189)	total: 13.3s	remaining: 626ms
191:	learn: 0.0003843	test: 0.0049437	best: 0.0049430 (189)	total: 13.4s	remaining: 557ms
192:	learn: 0.0003841	test: 0.0049427	best: 0.0049427 (192)	total: 13.4s	remaining: 488ms
193:	learn: 0.0003834	test: 0.0049431	best: 0.0049427 (192)	total: 13.5s	remaining: 418ms
194:	learn: 0.0003828	test: 0.0049423	best: 0.0049423 (194)	total: 13.6s	remaining: 349ms
195:	learn: 0.0003824	test: 0.0049422	best: 0.0049422 (195)	total: 13.7s	remaining: 279ms
196:	learn: 0.0003822	test: 0.0049413	best: 0.0049413 (196)	total: 13.7s	remaining: 209ms
197:	learn: 0.0003819	test: 0.0049409	best: 0.0049409 (197)	total: 13.8s	remaining: 140ms
198:	learn: 0.0003804	test: 0.0049407	best: 0.0049407 (198)	total: 13.9s	remaining: 69.8ms
199:	learn: 0.0003791	test: 0.0049405	best: 0.0049405 (199)	total: 14s	remaining: 0us

bestTest = 0

...

196:	learn: 0.0003300	test: 0.0040163	best: 0.0040163 (196)	total: 14s	remaining: 213ms
197:	learn: 0.0003298	test: 0.0040158	best: 0.0040158 (197)	total: 14s	remaining: 142ms
198:	learn: 0.0003294	test: 0.0040148	best: 0.0040148 (198)	total: 14.1s	remaining: 70.9ms
199:	learn: 0.0003291	test: 0.0040141	best: 0.0040141 (199)	total: 14.2s	remaining: 0us

bestTest = 0.00401414273
bestIteration = 199

iteration 0, bolt 1: MAPE=0.4014142772877852
0:	learn: 0.0005199	test: 0.0033537	best: 0.0033537 (0)	total: 93.6ms	remaining: 18.6s
1:	learn: 0.0005116	test: 0.0033409	best: 0.0033409 (1)	total: 158ms	remaining: 15.6s
2:	learn: 0.0005060	test: 0.0033366	best: 0.0033366 (2)	total: 224ms	remaining: 14.7s
3:	learn: 0.0004983	test: 0.0033243	best: 0.0033243 (3)	total: 288ms	remaining: 14.1s
4:	learn: 0.0004929	test: 0.0033204	best: 0.0033204 (4)	total: 357ms	remaining: 13.9s
5:	learn: 0.0004858	test: 0.0033086	best: 0.0033086 (5)	total: 419ms	remaining: 13.6s
6:	learn: 0.0004787	test: 0.0032939	

89:	learn: 0.0002399	test: 0.0029259	best: 0.0029259 (89)	total: 6.06s	remaining: 7.41s
90:	learn: 0.0002391	test: 0.0029253	best: 0.0029253 (90)	total: 6.13s	remaining: 7.34s
91:	learn: 0.0002383	test: 0.0029248	best: 0.0029248 (91)	total: 6.2s	remaining: 7.28s
92:	learn: 0.0002377	test: 0.0029235	best: 0.0029235 (92)	total: 6.26s	remaining: 7.21s
93:	learn: 0.0002372	test: 0.0029235	best: 0.0029235 (92)	total: 6.33s	remaining: 7.14s
94:	learn: 0.0002366	test: 0.0029223	best: 0.0029223 (94)	total: 6.4s	remaining: 7.08s
95:	learn: 0.0002359	test: 0.0029227	best: 0.0029223 (94)	total: 6.47s	remaining: 7.01s
96:	learn: 0.0002351	test: 0.0029223	best: 0.0029223 (94)	total: 6.54s	remaining: 6.94s
97:	learn: 0.0002346	test: 0.0029210	best: 0.0029210 (97)	total: 6.61s	remaining: 6.88s
98:	learn: 0.0002340	test: 0.0029215	best: 0.0029210 (97)	total: 6.67s	remaining: 6.81s
99:	learn: 0.0002328	test: 0.0029186	best: 0.0029186 (99)	total: 6.74s	remaining: 6.74s
100:	learn: 0.0002322	test: 0.0029

184:	learn: 0.0001997	test: 0.0028770	best: 0.0028770 (184)	total: 12.7s	remaining: 1.03s
185:	learn: 0.0001995	test: 0.0028767	best: 0.0028767 (185)	total: 12.8s	remaining: 961ms
186:	learn: 0.0001992	test: 0.0028763	best: 0.0028763 (186)	total: 12.8s	remaining: 893ms
187:	learn: 0.0001990	test: 0.0028759	best: 0.0028759 (187)	total: 12.9s	remaining: 825ms
188:	learn: 0.0001988	test: 0.0028758	best: 0.0028758 (188)	total: 13s	remaining: 757ms
189:	learn: 0.0001985	test: 0.0028761	best: 0.0028758 (188)	total: 13.1s	remaining: 688ms
190:	learn: 0.0001984	test: 0.0028761	best: 0.0028758 (188)	total: 13.1s	remaining: 619ms
191:	learn: 0.0001980	test: 0.0028762	best: 0.0028758 (188)	total: 13.2s	remaining: 551ms
192:	learn: 0.0001977	test: 0.0028758	best: 0.0028758 (192)	total: 13.3s	remaining: 482ms
193:	learn: 0.0001973	test: 0.0028754	best: 0.0028754 (193)	total: 13.4s	remaining: 413ms
194:	learn: 0.0001971	test: 0.0028750	best: 0.0028750 (194)	total: 13.4s	remaining: 345ms
195:	learn: 

77:	learn: 0.0001988	test: 0.0007023	best: 0.0007023 (77)	total: 5.8s	remaining: 9.07s
78:	learn: 0.0001961	test: 0.0006988	best: 0.0006988 (78)	total: 5.87s	remaining: 8.99s
79:	learn: 0.0001934	test: 0.0006932	best: 0.0006932 (79)	total: 5.94s	remaining: 8.91s
80:	learn: 0.0001908	test: 0.0006921	best: 0.0006921 (80)	total: 6.01s	remaining: 8.83s
81:	learn: 0.0001882	test: 0.0006880	best: 0.0006880 (81)	total: 6.08s	remaining: 8.75s
82:	learn: 0.0001857	test: 0.0006852	best: 0.0006852 (82)	total: 6.15s	remaining: 8.67s
83:	learn: 0.0001833	test: 0.0006802	best: 0.0006802 (83)	total: 6.22s	remaining: 8.59s
84:	learn: 0.0001809	test: 0.0006776	best: 0.0006776 (84)	total: 6.29s	remaining: 8.51s
85:	learn: 0.0001787	test: 0.0006767	best: 0.0006767 (85)	total: 6.36s	remaining: 8.43s


KeyboardInterrupt: 

We end up with the following feature set:

['days_since_start', 'Turbine_Pressure Drafttube', 'seconds_since_last_start', 'Netto Power', 'Turbine_Rotational Speed']